# Games Data Enginering

In [41]:
# Import the dependecies
import matplotlib.pyplot as plt
import pandas as pd
import scipy.stats as st
import sqlalchemy
from sqlalchemy import create_engine
from sqlalchemy import column, Integer, String, Float
from pymongo import MongoClient

In [42]:
#Read the games data and the study results
games_path = "data/games.csv"
games_data = pd.read_csv(games_path)
games_data.head(10)



AppID                                Name  Release date Estimated owners  \
0    20200                    Galactic Bowling  Oct 21, 2008        0 - 20000   
1   655370                        Train Bandit  Oct 12, 2017        0 - 20000   
2  1732930                        Jolt Project  Nov 17, 2021        0 - 20000   
3  1355720                            Henosis™  Jul 23, 2020        0 - 20000   
4  1139950               Two Weeks in Painland   Feb 3, 2020        0 - 20000   
5  1469160                      Wartune Reborn  Feb 26, 2021   50000 - 100000   
6  1659180                           TD Worlds   Jan 9, 2022        0 - 20000   
7  1968760  Legend of Rome - The Wrath of Mars   May 5, 2022        0 - 20000   
8  1178150               MazM: Jekyll and Hyde   Apr 2, 2020        0 - 20000   
9   320150           Deadlings: Rotten Edition  Nov 11, 2014   50000 - 100000   

   Peak CCU  Required age  Price  DLC count  \
0         0             0  19.99          0   
1         0             0   0.99          0   
2         0             0   4.99          0   
3         0             0   5.99          0   
4         0             0   0.00          0   
5        68             0   0.00          0   
6         3             0  10.99          1   
7         2             0   9.99          0   
8         1             0  14.99          0   
9         0             0   3.99          0   

                                      About the game  \
0  Galactic Bowling is an exaggerated and stylize...   
1  THE LAW!! Looks to be a showdown atop a train....   
2  Jolt Project: The army now has a new robotics ...   
3  HENOSIS™ is a mysterious 2D Platform Puzzler w...   
4  ABOUT THE GAME Play as a hacker who has arrang...   
5  Feel tired of auto-fight? Feel tired of boring...   
6  TD Worlds is a dynamic, highly strategical gam...   
7  When the Roman people honored a simple warrior...   
8  'MazM: Jekyll and Hyde' is a darkly entertaini...   
9  Death is lonely. He has zero friends on his Fa...   

                                 Supported languages  ...  \
0                                        ['English']  ...   
1  ['English', 'French', 'Italian', 'German', 'Sp...  ...   
2                 ['English', 'Portuguese - Brazil']  ...   
3  ['English', 'French', 'Italian', 'German', 'Sp...  ...   
4                     ['English', 'Spanish - Spain']  ...   
5                                        ['English']  ...   
6                   ['English', 'Russian', 'Danish']  ...   
7                              ['English', 'German']  ...   
8  ['English', 'French', 'Italian', 'German', 'Sp...  ...   
9  ['English', 'Polish', 'French', 'Italian', 'Ge...  ...   

  Average playtime two weeks Median playtime forever  \
0                          0                       0   
1                          0                       0   
2                          0                       0   
3                          0                       0   
4                          0                       0   
5                          0                       0   
6                          0                       0   
7                          0                       0   
8                          0                       0   
9                          0                     782   

  Median playtime two weeks             Developers             Publishers  \
0                         0  Perpetual FX Creative  Perpetual FX Creative   
1                         0           Rusty Moyher           Wild Rooster   
2                         0          Campião Games          Campião Games   
3                         0      Odd Critter Games      Odd Critter Games   
4                         0          Unusual Games          Unusual Games   
5                         0                  7Road                  7Road   
6                         0          MAKSIM VOLKAU          MAKSIM VOLKAU   
7                         0             magnussoft             magnussoft

In [43]:
app_desc_df = games_data.loc[:,['AppID', 'Name', 'About the game']]
app_desc_df.head(5)


AppID                   Name  \
0    20200       Galactic Bowling   
1   655370           Train Bandit   
2  1732930           Jolt Project   
3  1355720               Henosis™   
4  1139950  Two Weeks in Painland   

                                      About the game  
0  Galactic Bowling is an exaggerated and stylize...  
1  THE LAW!! Looks to be a showdown atop a train....  
2  Jolt Project: The army now has a new robotics ...  
3  HENOSIS™ is a mysterious 2D Platform Puzzler w...  
4  ABOUT THE GAME Play as a hacker who has arrang...

In [44]:
contact_df = games_data.loc[:,['AppID', 'Support url', 'Website', 'Support email']]
contact_df.head(5)

AppID                             Support url  \
0    20200                                     NaN   
1   655370                                     NaN   
2  1732930                                     NaN   
3  1355720                https://henosisgame.com/   
4  1139950  https://www.unusual-games.com/contact/   

                               Website                    Support email  
0       http://www.galacticbowling.net                              NaN  
1               http://trainbandit.com          support@rustymoyher.com  
2                                  NaN        ramoncampiaof31@gmail.com  
3             https://henosisgame.com/             info@henosisgame.com  
4  https://www.unusual-games.com/home/  welistentoyou@unusual-games.com

In [45]:
app_review_df = games_data.loc[:,['AppID', 'Recommendations', 'Notes', 'Positive', 'Negative']]
app_review_df.head(5)

AppID  Recommendations  \
0    20200                0   
1   655370                0   
2  1732930                0   
3  1355720                0   
4  1139950                0   

                                               Notes  Positive  Negative  
0                                                NaN         6        11  
1                                                NaN        53         5  
2                                                NaN         0         0  
3                                                NaN         3         0  
4  This Game may contain content not appropriate ...        50         8

In [46]:
app_detail_df = games_data.loc[:,['AppID', 'Release date', 'Price', 'Required age', 'Windows', 'Mac', 'Linux']]
app_detail_df.head(5)

AppID  Release date  Price  Required age  Windows    Mac  Linux
0    20200  Oct 21, 2008  19.99             0     True  False  False
1   655370  Oct 12, 2017   0.99             0     True   True  False
2  1732930  Nov 17, 2021   4.99             0     True  False  False
3  1355720  Jul 23, 2020   5.99             0     True   True   True
4  1139950   Feb 3, 2020   0.00             0     True   True  False

In [47]:
app_dsc_df.to_csv('app_dsc.csv', index = False)
contact_df.to_csv('contact.csv', index = False)
app_review_df.to_csv('app_review.csv', index = False)

In [48]:
# Make a connection 
# Connect to MongoDB
client = MongoClient('localhost', 27017)
db = client.Gamesdata
collection = db.app_description


In [52]:
app_desc_df.reset_index(inplace=False)
data_dict = app_desc_df.to_dict("records")
data_dict

[{'AppID': 20200,
  'Name': 'Galactic Bowling',
  'About the game': 'Galactic Bowling is an exaggerated and stylized bowling game with an intergalactic twist. Players will engage in fast-paced single and multi-player competition while being submerged in a unique new universe filled with over-the-top humor, wild characters, unique levels, and addictive game play. The title is aimed at players of all ages and skill sets. Through accessible and intuitive controls and game-play, Galactic Bowling allows you to jump right into the action. A single-player campaign and online play allow you to work your way up the ranks of the Galactic Bowling League! Whether you have hours to play or only a few minutes, Galactic Bowling is a fast paced and entertaining experience that will leave you wanting more! Full Single-player story campaign including 11 Characters and Environments. 2 Single-player play modes including Regular and Battle Modes. Head to Head Online Multiplayer play Modes. Super Powers, Sp

In [50]:
collection.insert_many(data_dict)

InsertManyResult([ObjectId('66947321fe19ceee8ea959dc'), ObjectId('66947321fe19ceee8ea959dd'), ObjectId('66947321fe19ceee8ea959de'), ObjectId('66947321fe19ceee8ea959df'), ObjectId('66947321fe19ceee8ea959e0'), ObjectId('66947321fe19ceee8ea959e1'), ObjectId('66947321fe19ceee8ea959e2'), ObjectId('66947321fe19ceee8ea959e3'), ObjectId('66947321fe19ceee8ea959e4'), ObjectId('66947321fe19ceee8ea959e5'), ObjectId('66947321fe19ceee8ea959e6'), ObjectId('66947321fe19ceee8ea959e7'), ObjectId('66947321fe19ceee8ea959e8'), ObjectId('66947321fe19ceee8ea959e9'), ObjectId('66947321fe19ceee8ea959ea'), ObjectId('66947321fe19ceee8ea959eb'), ObjectId('66947321fe19ceee8ea959ec'), ObjectId('66947321fe19ceee8ea959ed'), ObjectId('66947321fe19ceee8ea959ee'), ObjectId('66947321fe19ceee8ea959ef'), ObjectId('66947321fe19ceee8ea959f0'), ObjectId('66947321fe19ceee8ea959f1'), ObjectId('66947321fe19ceee8ea959f2'), ObjectId('66947321fe19ceee8ea959f3'), ObjectId('66947321fe19ceee8ea959f4'), ObjectId('66947321fe19ceee8ea959